# Class05a - Prediction using Decision Tree (using Default Parameters)

## Introduction and Overview


In this project, we will be using a dataset containing census information from [UCI's Machine Learning Repository](https://archive.ics.uci.edu/ml/datasets/census+income).

Our prediction task is to determine whether a person makes over 50K a year. We are given the input variables that include measures of age, working class, education, edcuational number, marital status, accupation, relationship, race, sex, capital-gain, capital loss, hours worked per week

In this notebook we will use a decision tree to predict whether a persons income is greater than $50k using the input variables age, sex, capital-gain, capital-loss, hours-per-week.

Let's get started!


# Predicting Income with Decision Tree



## Step 1: Install and import necessary packages

In [1]:
# import packages
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import confusion_matrix, accuracy_score, precision_score, recall_score
import numpy as np
from sklearn.preprocessing import OrdinalEncoder
from sklearn.preprocessing import LabelEncoder


## Step 2: Load, clean and prepare data


### 2.1 Read data (income.csv)

In [2]:
income_df = pd.read_csv("../Data/income.csv")
income_df.head(5)

age          workclass   fnlwgt   education   education-num  \
0   39          State-gov    77516   Bachelors              13   
1   50   Self-emp-not-inc    83311   Bachelors              13   
2   38            Private   215646     HS-grad               9   
3   53            Private   234721        11th               7   
4   28            Private   338409   Bachelors              13   

        marital-status          occupation    relationship    race      sex  \
0        Never-married        Adm-clerical   Not-in-family   White     Male   
1   Married-civ-spouse     Exec-managerial         Husband   White     Male   
2             Divorced   Handlers-cleaners   Not-in-family   White     Male   
3   Married-civ-spouse   Handlers-cleaners         Husband   Black     Male   
4   Married-civ-spouse      Prof-specialty            Wife   Black   Female   

    capital-gain   capital-loss   hours-per-week  native-country  income  
0           2174              0               40   United-States   <=50K  
1              0              0               13   United-States   <=50K  
2              0              0               40   United-States   <=50K  
3              0              0               40   United-States   <=50K  
4              0              0               40            Cuba   <=50K

### 2.2 Explore the dataset

In [3]:
income_df.columns

Index(['age', ' workclass', ' fnlwgt', ' education', ' education-num',
       ' marital-status', ' occupation', ' relationship', ' race', ' sex',
       ' capital-gain', ' capital-loss', ' hours-per-week', ' native-country',
       ' income'],
      dtype='object')

In [4]:
income_df.describe()

age        fnlwgt   education-num   capital-gain  \
count  32561.000000  3.256100e+04    32561.000000   32561.000000   
mean      38.581647  1.897784e+05       10.080679    1077.648844   
std       13.640433  1.055500e+05        2.572720    7385.292085   
min       17.000000  1.228500e+04        1.000000       0.000000   
25%       28.000000  1.178270e+05        9.000000       0.000000   
50%       37.000000  1.783560e+05       10.000000       0.000000   
75%       48.000000  2.370510e+05       12.000000       0.000000   
max       90.000000  1.484705e+06       16.000000   99999.000000   

        capital-loss   hours-per-week  
count   32561.000000     32561.000000  
mean       87.303830        40.437456  
std       402.960219        12.347429  
min         0.000000         1.000000  
25%         0.000000        40.000000  
50%         0.000000        40.000000  
75%         0.000000        45.000000  
max      4356.000000        99.000000

In [5]:
income_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 32561 entries, 0 to 32560
Data columns (total 15 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   age              32561 non-null  int64 
 1    workclass       32561 non-null  object
 2    fnlwgt          32561 non-null  int64 
 3    education       32561 non-null  object
 4    education-num   32561 non-null  int64 
 5    marital-status  32561 non-null  object
 6    occupation      32561 non-null  object
 7    relationship    32561 non-null  object
 8    race            32561 non-null  object
 9    sex             32561 non-null  object
 10   capital-gain    32561 non-null  int64 
 11   capital-loss    32561 non-null  int64 
 12   hours-per-week  32561 non-null  int64 
 13   native-country  32561 non-null  object
 14   income          32561 non-null  object
dtypes: int64(6), object(9)
memory usage: 3.7+ MB


### 2.3 Clean/transform data (where necessary)

Based on findings from data exploration, we need to clean up colum names, as there are some leading whitespace characters. For convenience, we may also want to change dashes to underscore.

In [6]:
income_df.columns = [s.strip().replace('-', '_') for s in income_df.columns] 
income_df.columns

Index(['age', 'workclass', 'fnlwgt', 'education', 'education_num',
       'marital_status', 'occupation', 'relationship', 'race', 'sex',
       'capital_gain', 'capital_loss', 'hours_per_week', 'native_country',
       'income'],
      dtype='object')

Check for missing values

In [7]:
income_df.isnull().sum()

age               0
workclass         0
fnlwgt            0
education         0
education_num     0
marital_status    0
occupation        0
relationship      0
race              0
sex               0
capital_gain      0
capital_loss      0
hours_per_week    0
native_country    0
income            0
dtype: int64

Check for categorical variables

In [8]:
income_df.sex.unique()

array([' Male', ' Female'], dtype=object)

Though Decision Trees are able to handle both numerical and categorical data, the scikit-learn implementation does not support categorical variables for now. Therefore, instead of categorical change values to numeric.

In [9]:
enc = OrdinalEncoder()
income_df.sex = enc.fit_transform(income_df[['sex']])
income_df.head(20)

age          workclass  fnlwgt      education  education_num  \
0    39          State-gov   77516      Bachelors             13   
1    50   Self-emp-not-inc   83311      Bachelors             13   
2    38            Private  215646        HS-grad              9   
3    53            Private  234721           11th              7   
4    28            Private  338409      Bachelors             13   
5    37            Private  284582        Masters             14   
6    49            Private  160187            9th              5   
7    52   Self-emp-not-inc  209642        HS-grad              9   
8    31            Private   45781        Masters             14   
9    42            Private  159449      Bachelors             13   
10   37            Private  280464   Some-college             10   
11   30          State-gov  141297      Bachelors             13   
12   23            Private  122272      Bachelors             13   
13   32            Private  205019     Assoc-acdm             12   
14   40            Private  121772      Assoc-voc             11   
15   34            Private  245487        7th-8th              4   
16   25   Self-emp-not-inc  176756        HS-grad              9   
17   32            Private  186824        HS-grad              9   
18   38            Private   28887           11th              7   
19   43   Self-emp-not-inc  292175        Masters             14   

            marital_status          occupation    relationship  \
0            Never-married        Adm-clerical   Not-in-family   
1       Married-civ-spouse     Exec-managerial         Husband   
2                 Divorced   Handlers-cleaners   Not-in-family   
3       Married-civ-spouse   Handlers-cleaners         Husband   
4       Married-civ-spouse      Prof-specialty            Wife   
5       Married-civ-spouse     Exec-managerial            Wife   
6    Married-spouse-absent       Other-service   Not-in-family   
7       Married-civ-spouse     Exec-managerial         Husband   
8            Never-married      Prof-specialty   Not-in-family   
9       Married-civ-spouse     Exec-managerial         Husband   
10      Married-civ-spouse     Exec-managerial         Husband   
11      Married-civ-spouse      Prof-specialty         Husband   
12           Never-married        Adm-clerical       Own-child   
13           Never-married               Sales   Not-in-family   
14      Married-civ-spouse        Craft-repair         Husband   
15      Married-civ-spouse    Transport-moving         Husband   
16           Never-married     Farming-fishing       Own-child   
17           Never-married   Machine-op-inspct       Unmarried   
18      Married-civ-spouse               Sales         Husband   
19                Divorced     Exec-managerial       Unmarried   

                   race  sex  capital_gain  capital_loss  hours_per_week  \
0                 White  1.0          2174             0              40   
1                 White  1.0             0             0              13   
2                 White  1.0             0             0              40   
3                 Black  1.0             0             0              40   
4                 Black  0.0             0             0              40   
5                 White  0.0             0             0              40   
6                 Black  0.0             0             0              16   
7                 White  1.0             0             0              45   
8                 White  0.0         14084             0              50   
9                 White  1.0          5178             0              40   
10                Black  1.0             0             0              80   
11   Asian-Pac-Islander  1.0             0             0              40   
12                White  0.0             0             0              30   
13                Black  1.0             0             0              50   
14   Asian-Pac-Islander  1.0             0      

Or, we could manually encode by doing something like the following....

In [10]:
#income_df.sex = income_df.sex.replace("Male", 0, regex=True)
#income_df.sex = income_df.sex.replace("Female", 1, regex=True)
#income_df.sex

In [11]:
# Transform our predictors into integers. This is necessary if we later want to test precision and recall. 
income_df.income.unique()

array([' <=50K', ' >50K'], dtype=object)

In [12]:
enc = LabelEncoder()
income_df.income = enc.fit_transform(income_df['income'])
income_df.head(20)

age          workclass  fnlwgt      education  education_num  \
0    39          State-gov   77516      Bachelors             13   
1    50   Self-emp-not-inc   83311      Bachelors             13   
2    38            Private  215646        HS-grad              9   
3    53            Private  234721           11th              7   
4    28            Private  338409      Bachelors             13   
5    37            Private  284582        Masters             14   
6    49            Private  160187            9th              5   
7    52   Self-emp-not-inc  209642        HS-grad              9   
8    31            Private   45781        Masters             14   
9    42            Private  159449      Bachelors             13   
10   37            Private  280464   Some-college             10   
11   30          State-gov  141297      Bachelors             13   
12   23            Private  122272      Bachelors             13   
13   32            Private  205019     Assoc-acdm             12   
14   40            Private  121772      Assoc-voc             11   
15   34            Private  245487        7th-8th              4   
16   25   Self-emp-not-inc  176756        HS-grad              9   
17   32            Private  186824        HS-grad              9   
18   38            Private   28887           11th              7   
19   43   Self-emp-not-inc  292175        Masters             14   

            marital_status          occupation    relationship  \
0            Never-married        Adm-clerical   Not-in-family   
1       Married-civ-spouse     Exec-managerial         Husband   
2                 Divorced   Handlers-cleaners   Not-in-family   
3       Married-civ-spouse   Handlers-cleaners         Husband   
4       Married-civ-spouse      Prof-specialty            Wife   
5       Married-civ-spouse     Exec-managerial            Wife   
6    Married-spouse-absent       Other-service   Not-in-family   
7       Married-civ-spouse     Exec-managerial         Husband   
8            Never-married      Prof-specialty   Not-in-family   
9       Married-civ-spouse     Exec-managerial         Husband   
10      Married-civ-spouse     Exec-managerial         Husband   
11      Married-civ-spouse      Prof-specialty         Husband   
12           Never-married        Adm-clerical       Own-child   
13           Never-married               Sales   Not-in-family   
14      Married-civ-spouse        Craft-repair         Husband   
15      Married-civ-spouse    Transport-moving         Husband   
16           Never-married     Farming-fishing       Own-child   
17           Never-married   Machine-op-inspct       Unmarried   
18      Married-civ-spouse               Sales         Husband   
19                Divorced     Exec-managerial       Unmarried   

                   race  sex  capital_gain  capital_loss  hours_per_week  \
0                 White  1.0          2174             0              40   
1                 White  1.0             0             0              13   
2                 White  1.0             0             0              40   
3                 Black  1.0             0             0              40   
4                 Black  0.0             0             0              40   
5                 White  0.0             0             0              40   
6                 Black  0.0             0             0              16   
7                 White  1.0             0             0              45   
8                 White  0.0         14084             0              50   
9                 White  1.0          5178             0              40   
10                Black  1.0             0             0              80   
11   Asian-Pac-Islander  1.0             0             0              40   
12                White  0.0             0             0              30   
13                Black  1.0             0             0              50   
14   Asian-Pac-Islander  1.0             0      

In [13]:
# income_df.income = income_df.income.replace("<=50K", 0, regex=True)
# income_df.income = income_df.income.replace(">50K", 1, regex=True)

## Step 3 Split data intro training and validation sets

Split our data variables into predictors (input) and target.

In [14]:
target = 'income'
predictors = ['age', 'sex', 'capital_gain', 'capital_loss', 'hours_per_week']
X = income_df[predictors]
y = income_df[target]

Create the training set and the test set with a 70/30 split.

In [15]:
train_X, valid_X, train_y, valid_y = train_test_split(X,y, test_size=0.3, random_state=1)

## Step 4: Create and train model


You can find details about the DecisionTreeClassifier [here](https://scikit-learn.org/stable/modules/generated/sklearn.tree.DecisionTreeClassifier.html).

### 4.1 Create a decision tree using the default parameters

In [16]:
dtree=DecisionTreeClassifier(random_state=1)

### 4.2 Fit the model to the training data

In [17]:
dtree.fit(train_X, train_y)

DecisionTreeClassifier(random_state=1)

### 4.3 Review of the performance of the model on the validation/test data

In [18]:
validation_predictions = dtree.predict(valid_X)

print('Confusion Matrix:\n ', confusion_matrix(valid_y, validation_predictions))
print('Accuracy score:\n', accuracy_score(valid_y, validation_predictions))
print('Precision score:\n', precision_score(valid_y, validation_predictions))
print('Recall score:\n', recall_score(valid_y, validation_predictions))

Confusion Matrix:
  [[7127  423]
 [1291  928]]
Accuracy score:
 0.8245470365441704
Precision score:
 0.6868985936343449
Recall score:
 0.4182063992789545


In [19]:
train_predictions = dtree.predict(train_X)

print('Confusion Matrix:\n', confusion_matrix(train_y, train_predictions))
print('Accuracy score:\n', accuracy_score(train_y, train_predictions))
print('Precision score:\n', precision_score(train_y, train_predictions))
print('Recall score:\n', recall_score(train_y, train_predictions))

Confusion Matrix:
 [[16700   470]
 [ 2843  2779]]
Accuracy score:
 0.8546419796419796
Precision score:
 0.8553401046475839
Recall score:
 0.4943080754180007


## Step 5: Deploy model

In this notebook we develop a model and test its performance on the validation data. In this exercise (predicting income), there is no model deployment. 

What does "deploying" a model mean? Up to this point, we've trained a model to our training data and then estimated the performance of this model on new data by testing its performance on validation data.

In this course, we finish after building the model. In practice, the model is used by an organization/company in some way. Using the model is often referred to as "deploying" the model.

How a model is deployed can vary. It may simply be deployed as a notebook that reads the latest predictor data and uses the developed model to make predictions. The model can also be deployed inside enterprise decision support software that automatically makes predictions on incoming data.

## Visualizing a Decision Tree

There are a number of ways we can visualize our tree result...

### As a plot

We can create a visual representation of the tree using sklearn's plot_tree function. 

WARNING: For complex decision trees (which, as you will see, is a complex tree) this visualization can take as much as a few minutes to produce. 

> NOTE: The decision tree produced from this analysis is very large. Visualizing a tree this large doesn't add much information and isn't necessary. Next class we will see techniques to limit the size of the tree and more easily visualize trees. I've commenteed out this code, but you can uncomment and try running (depending on the power of your computer, it may take minutes for this cell to finish processing).

In [20]:
from sklearn.tree import plot_tree
import matplotlib.pyplot as plt

fig = plt.figure(figsize=(100,100))
_ = plot_tree(dtree, 
                feature_names=X.columns,  
                class_names=['<=$50k', '>$50k'],
                filled=True,
                fontsize=8
             )



### As Text

In [21]:
from sklearn.tree import export_text

text_representation = export_text(dtree)

print(text_representation)

|--- feature_2 <= 5119.00
|   |--- feature_0 <= 30.50
|   |   |--- feature_0 <= 25.50
|   |   |   |--- feature_3 <= 2116.00
|   |   |   |   |--- feature_0 <= 23.50
|   |   |   |   |   |--- feature_4 <= 45.50
|   |   |   |   |   |   |--- feature_0 <= 20.50
|   |   |   |   |   |   |   |--- class: 0
|   |   |   |   |   |   |--- feature_0 >  20.50
|   |   |   |   |   |   |   |--- feature_4 <= 31.00
|   |   |   |   |   |   |   |   |--- class: 0
|   |   |   |   |   |   |   |--- feature_4 >  31.00
|   |   |   |   |   |   |   |   |--- feature_4 <= 32.50
|   |   |   |   |   |   |   |   |   |--- feature_0 <= 22.50
|   |   |   |   |   |   |   |   |   |   |--- feature_0 <= 21.50
|   |   |   |   |   |   |   |   |   |   |   |--- class: 0
|   |   |   |   |   |   |   |   |   |   |--- feature_0 >  21.50
|   |   |   |   |   |   |   |   |   |   |   |--- truncated branch of depth 2
|   |   |   |   |   |   |   |   |   |--- feature_0 >  22.50
|   |   |   |   |   |   |   |   |   |   |--- class: 0
|   |   |  